In [ ]:
import math
import os
import sys
from typing import List

import pandas as pd
from langchain_core.documents import Document

sys.path.append(os.path.abspath(os.path.join(os.getcwd(), "..")))
from habr_rag.splitter import MarkdownSplitter

try:
    df = pd.read_csv("../data/raw/habr_dataset.csv")
except FileNotFoundError:
    print("habr_dataset.csv not found in ../data/raw/. Please ensure it exists.")
    try:
        df = pd.read_csv("habr_dataset.csv")
    except:
        pass

if "df" in locals():
    splitter = MarkdownSplitter(
        chunk_size=500,
        chunk_overlap=50,
        multi_process=True,
        show_progress=True,
        include_metadata=("title", "author", "hubs", "flows", "tags", "labels"),
    )


In [ ]:
cols_to_remove = [
    "text_html",
    "original_author",
    "original_url",
    "lead_html",
    "lead_markdown",
    "time_published",
    "comments",
]
df.drop(columns=cols_to_remove, inplace=True, errors="ignore")

In [ ]:
def load_documents_from_df(df: pd.DataFrame) -> List[Document]:
    if "text_markdown" not in df.columns:
        raise ValueError(
            f"Column 'text_markdown' not found in DataFrame. Available columns: {df.columns.tolist()}"
        )

    documents = []

    metadata_columns = [col for col in df.columns if col != "text_markdown"]

    for _, row in df.iterrows():
        content = row.get("text_markdown")
        if pd.isna(content):
            content = ""
        else:
            content = str(content)

        metadata = {}
        for col in metadata_columns:
            val = row[col]

            if isinstance(val, float) and math.isnan(val):
                metadata[col] = None
            else:
                metadata[col] = val

        doc = Document(page_content=content, metadata=metadata)
        documents.append(doc)

    return documents


In [ ]:
habr_documents = load_documents_from_df(df)

In [ ]:
splitted_habr_documents = splitter.split_documents(habr_documents, keep_tables=True)

Сплит документов: 100%|██████████| 20/20 [00:00<00:00, 32.73it/s]


In [ ]:
from pprint import pprint

pprint(splitted_habr_documents[0].metadata, indent=2)

{ 'author': 'DJP',
  'chunk_id': 'de891f14-3328-4482-914f-37df9753f053',
  'complexity': None,
  'flows': "['develop' 'popsci']",
  'format': None,
  'hubs': "['arduino' 'DIY' 'autogadgets' 'health']",
  'id': 422637,
  'initial_text': 'По данным ГИБДД за прошлый, 2017й год в ДТП с участием '
                  'водителей, находящихся в состоянии опьянения, погибло более '
                  '3х тысяч и ранено более 17 тысяч россиян.\n'
                  'Это не только значительные потери для государства и '
                  'общества, но и, в первую очередь конечно же, огромная, '
                  'порой невосполнимая утрата для родных и близких. И никто от '
                  'этого не застрахован.\n'
                  'Да, нам обещают скорую, быстрее, чем мы думаем, замену '
                  'водителей на роботов, но пока этого не произошло и люди '
                  'продолжают гибнуть.\n'
                  'Что же, попробуем сейчас предложить решение этой проблемы.\n'
           

In [ ]:
import os
import pickle

output_path = "../data/processed/chunked_docs.pkl"
os.makedirs(os.path.dirname(output_path), exist_ok=True)

with open(output_path, "wb") as f:
    pickle.dump(splitted_habr_documents, f)

In [ ]:
with open("../data/processed/chunked_docs.pkl", "rb") as f:
    a = pickle.load(f)

a

[Document(metadata={'id': 422637, 'language': 'ru', 'url': 'https://habr.com/ru/post/422637/', 'title': 'Подарок гика: защита от автоАлкаша', 'author': 'DJP', 'type': 'article', 'statistics': "{'commentsCount': 124, 'favoritesCount': 6, 'readingCount': 9766, 'score': -8, 'votesCount': 42, 'votesCountPlus': 17, 'votesCountMinus': 25}", 'labels': "['recovery' 'sandbox']", 'hubs': "['arduino' 'DIY' 'autogadgets' 'health']", 'flows': "['develop' 'popsci']", 'tags': "['arduino' 'безопасность' 'автомобиль' 'алкоголь']", 'reading_time': 10.0, 'format': None, 'complexity': None, 'initial_text': 'По данным ГИБДД за прошлый, 2017й год в ДТП с участием водителей, находящихся в состоянии опьянения, погибло более 3х тысяч и ранено более 17 тысяч россиян.\nЭто не только значительные потери для государства и общества, но и, в первую очередь конечно же, огромная, порой невосполнимая утрата для родных и близких. И никто от этого не застрахован.\nДа, нам обещают скорую, быстрее, чем мы думаем, замену во